In [28]:
import numpy as np 
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json 
!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim 
import requests
from pandas.io.json import json_normalize 
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium

Solving environment: done

# All requested packages already installed.



In [360]:
df_to = pd.read_csv('/Users/Richard/Desktop/Trontogeolist.csv')
df_to = df_to.drop(columns = 'Unnamed: 0')
df_to

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
5           M9A         Etobicoke   
6           M1B       Scarborough   
7           M3B        North York   
8           M4B         East York   
9           M5B  Downtown Toronto   
10          M6B        North York   
11          M9B         Etobicoke   
12          M1C       Scarborough   
13          M3C        North York   
14          M4C         East York   
15          M5C  Downtown Toronto   
16          M6C              York   
17          M9C         Etobicoke   
18          M1E       Scarborough   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
21          M6E              York   
22          M1G       Scarborough   
23          M4G         East York   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
26          M1H       Scarborough   
27          M2H        North York   
28          M3H        North York   
29          M4H         East York   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
32          M1J       Scarborough   
33          M2J        North York   
34          M3J        North York   
35          M4J         East York   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
38          M1K       Scarborough   
39          M2K        North York   
40          M3K        North York   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
44          M1L       Scarborough   
45          M2L        North York   
46          M3L        North York   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
49          M6L        North York   
50          M9L        North York   
51          M1M       Scarborough   
52          M2M        North York   
53          M3M        North York   
54          M4M      East Toronto   
55          M5M        North York   
56          M6M              York   
57          M9M        North York   
58          M1N       Scarborough   
59          M2N        North York   
60          M3N        North York   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
63          M6N              York   
64          M9N              York   
65          M1P       Scarborough   
66          M2P        North York   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
70          M9P         Etobicoke   
71          M1R       Scarborough   
72          M2R        North York   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
76          M7R       Mississauga   
77          M9R         Etobicoke   
78          M1S       Scarborough   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
82          M1T       Scarborough   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
85          M1V       Scarborough   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
88          M8V         Etobicoke   
89          M9V         Etobicoke   
90          M1W       Scarborough   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
93          M8W         Etobicoke   
94          M9W         Etobicoke   
95          M1X       Scarborough   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                 

In [6]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [7]:
neighborhoods_data = newyork_data['features']

In [13]:
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

neighborhoods = pd.DataFrame(columns=column_names)

In [14]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [17]:
df_ny = neighborhoods

In [481]:
df_ny.shape

(306, 4)

In [482]:
df_to.shape

(102, 5)

In [20]:
df_to.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 102 entries, 0 to 101
Data columns (total 5 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Postal Code   102 non-null    object 
 1   Borough       102 non-null    object 
 2   Neighborhood  102 non-null    object 
 3   Latitude      102 non-null    float64
 4   Longitude     102 non-null    float64
dtypes: float64(2), object(3)
memory usage: 4.1+ KB


In [22]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df_to['Borough'].unique()),
        df_to.shape[0]
    )
)

The dataframe has 10 boroughs and 102 neighborhoods.


In [33]:
address = 'Toronto,ON'

geolocator_to = Nominatim(user_agent="ny_explorer")
location_to = geolocator_to.geocode(address)
latitude_to = location_to.latitude
longitude_to = location_to.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude_to, longitude_to))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [23]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df_ny['Borough'].unique()),
        df_ny.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [31]:
address = 'New York City, NY'

geolocator_ny = Nominatim(user_agent="ny_explorer")
location_ny = geolocator_ny.geocode(address)
latitude_ny = location_ny.latitude
longitude_ny = location_ny.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude_ny, longitude_ny))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [41]:
map_newyork = folium.Map(location=[latitude_ny, longitude_ny], zoom_start=10.5)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_ny['Latitude'], df_ny['Longitude'], df_ny['Borough'], df_ny['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [45]:
map_toronto = folium.Map(location=[latitude_to, longitude_to], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_to['Latitude'], df_to['Longitude'], df_to['Borough'], df_to['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [89]:
CLIENT_ID = '4HEIOOTCVWJC31B12GMPUZKSOMWHTUONAM0A55XPAC4XQVGR' # your Foursquare ID
CLIENT_SECRET = 'RWWQMPZXEKNZXJN5C23D2MTXVJZ0OI3421OIBLX2XBRFZTDJ' # your Foursquare Secret
VERSION = '20200605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 4HEIOOTCVWJC31B12GMPUZKSOMWHTUONAM0A55XPAC4XQVGR
CLIENT_SECRET:RWWQMPZXEKNZXJN5C23D2MTXVJZ0OI3421OIBLX2XBRFZTDJ


In [90]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [91]:

newyork_venues = getNearbyVenues(names=df_ny['Neighborhood'],
                                   latitudes=df_ny['Latitude'],
                                   longitudes=df_ny['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [92]:

toronto_venues = getNearbyVenues(names=df_to['Neighborhood'],
                                   latitudes=df_to['Latitude'],
                                   longitudes=df_to['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [93]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 426 uniques categories.


In [94]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 264 uniques categories.


In [373]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      34                      34   
Annadale                                      13                      13   
Arden Heights                                  4                       4   
Arlington                                      8                       8   
Arrochar                                      21                      21   
Arverne                                       20                      20   
Astoria                                      100                     100   
Astoria Heights                               12                      12   
Auburndale                                    19                      19   
Bath Beach                                    50                      50   
Battery Park City                             68                      68   
Bay Ridge                                     84                      84   
Bay Terrace                                   49                      49   
Baychester                                    22                      22   
Bayside                                       76                      76   
Bayswater                                      1                       1   
Bedford Park                                  38                      38   
Bedford Stuyvesant                            29                      29   
Beechhurst                                    15                      15   
Bellaire                                      13                      13   
Belle Harbor                                  17                      17   
Bellerose                                     24                      24   
Belmont                                      100                     100   
Bensonhurst                                   28                      28   
Bergen Beach                                   6                       6   
Blissville                                    16                      16   
Bloomfield                                     4                       4   
Boerum Hill                                   88                      88   
Borough Park                                  24                      24   
Breezy Point                                   6                       6   
Briarwood                                      8                       8   
Brighton Beach                                44                      44   
Broad Channel                                  6                       6   
Broadway Junction                             15                      15   
Bronxdale                                     13                      13   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   15                      15   
Bulls Head                                    45                      45   
Bushwick                                      72                      72   
Butler Manor                                   7                       7   
Cambria Heights                               13                      13   
Canarsie                                       5                       5   
Carnegie Hill                                 95                      95   
Carroll Gardens                              100                     100   
Castle Hill                                    9                       9   
Castleton Corners                             17                      17   
Central Harlem                                45                      45   
Charleston                                    31                      31   
Chelsea                                      105                     105   
Chinatown                                    100                     100   

In [374]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               4   
Alderwood, Long Branch                                                  8   
Bathurst Manor, Wilson Heights, Downsview North                        21   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      25   
Berczy Park                                                            57   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           24   
Business reply mail Processing Centre, South Ce...                     17   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Caledonia-Fairbanks                                                     4   
Canada Post Gateway Processing Centre                                  13   
Cedarbrae                                                               8   
Central Bay Street                                                     70   
Christie                                                               17   
Church and Wellesley                                                   71   
Clarks Corners, Tam O'Shanter, Sullivan                                12   
Cliffside, Cliffcrest, Scarborough Village West                         2   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             33   
Davisville North                                                        7   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills                                                              27   
Dorset Park, Wexford Heights, Scarborough Town ...                      6   
Downsview                                                              16   
Dufferin, Dovercourt Village                                           14   
East Toronto, Broadview North (Old East York)                           2   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      8   
Fairview, Henry Farm, Oriole                                           65   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         5   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                         9   
Guildwood, Morningside, West Hill                                       8   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
Hillcrest Village                                                       5   
Humber Summit                                                           2   
Humberlea, Emery                                                        2   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         19   
Kennedy Park, Ionview, East Birchmount Park                             6   
Kensington Market, Chinatown, Grange Park                              65   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                                       14   
Lawrence Park                                                           4   
Leaside                                                                33   
Little Portugal, Trinity                                               44   
Malvern, Rouge                                                          1   
Milliken, Agincourt North, Steeles East, L'Amor.

In [375]:
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head(5)

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                0          0           0           0       0     0    0   
1                0          0           0           0       0     0    0   
2                0          0           0           0       0     0    0   
3                0          0           0           0       0     0    0   
4                0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Bath House  Beach  \
0               0                 0                 0           0      0   
1               0                 0                 0           0      0   
2               0                 0                 0           0      0   
3               0                 0                 0           0      0   
4               0                 0                 0           0      0   

   Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0          0                0         0            0           0   
1          0                0         0            0           0   
2          0                0         0            0           0   
3          0                0         0            0           0   
4          0                0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0          0           0       0   
4              0            

In [376]:
newyork_onehot.shape

(10155, 426)

In [377]:
ny_ground = newyork_onehot.groupby('Neighborhood').mean().reset_index()
ny_ground.head(5)

Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0       Allerton          0.0                0.0             0.0   
1       Annadale          0.0                0.0             0.0   
2  Arden Heights          0.0                0.0             0.0   
3      Arlington          0.0                0.0             0.0   
4       Arrochar          0.0                0.0             0.0   

   Afghan Restaurant  African Restaurant  Airport Terminal  \
0                0.0                 0.0               0.0   
1                0.0                 0.0               0.0   
2                0.0                 0.0               0.0   
3                0.0                 0.0               0.0   
4                0.0                 0.0               0.0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0             0.000000           0.0     0.0               0.0   
1             0.076923           0.0     0.0               0.0   
2             0.000000           0.0     0.0               0.0   
3             0.125000           0.0     0.0               0.0   
4             0.000000           0.0     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                   0.0               0.0            0.000000         0.0   
1                   0.0               0.0            0.000000         0.0   
2                   0.0               0.0            0.000000         0.0   
3                   0.0               0.0            0.000000         0.0   
4                   0.0               0.0            0.047619         0.0   

   Australian Restaurant  Austrian Restaurant  Automotive Shop  BBQ Joint  \
0                    0.0                  0.0              0.0        0.0   
1                    0.0                  0.0              0.0        0.0   
2                    0.0                  0.0              0.0        0.0   
3                    0.0                  0.0              0.0        0.0   
4                    0.0                  0.0              0.0        0.0   

   Baby Store  Bagel Shop    Bakery  Bank       Bar  Baseball Field  \
0         0.0    0.000000  0.058824   0.0  0.000000             0.0   
1         0.0    0.000000  0.000000   0.0  0.076923             0.0   
2         0.0    0.000000  0.000000   0.0  0.000000             0.0   
3         0.0    0.000000  0.000000   0.0  0.000000             0.0   
4         0.0    0.047619  0.000000   0.0  0.000000             0.0   

   Baseball Stadium  Basketball Court  Bath House  Beach  Beach Bar  \
0               0.0               0.0         0.0    0.0        0.0   
1               0.0               0.0         0.0    0.0        0.0   
2               0.0               0.0         0.0    0.0        0.0   
3               0.0               0.0         0.0    0.0        0.0   
4               0.0               0.0         0.0    0.0        0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0              0.0       0.0          0.0         0.0            0.0   
1              0.0       0.0          0.0         0.0            0.0   
2              0.0       0.0          0.0         0.0            0.0   
3              0.0       0.0          0.0         0.0            0.0   
4              0.0       0.0          0.0         0.0            0.0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                       0.0        0.0         0.0     0.0         0.0   
1            

In [378]:
filt = [x for x in ny_ground.columns[ny_ground.columns.str.contains('Restaurant')]]

In [379]:
ny_rest = ny_ground[filt]
ny_restaurant = pd.concat([ny_ground['Neighborhood'],ny_rest],axis = 1,sort = False)


In [380]:
ny_restaurant.head(5)

Neighborhood  Afghan Restaurant  African Restaurant  American Restaurant  \
0       Allerton                0.0                 0.0             0.000000   
1       Annadale                0.0                 0.0             0.076923   
2  Arden Heights                0.0                 0.0             0.000000   
3      Arlington                0.0                 0.0             0.125000   
4       Arrochar                0.0                 0.0             0.000000   

   Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  \
0               0.0                     0.0               0.0   
1               0.0                     0.0               0.0   
2               0.0                     0.0               0.0   
3               0.0                     0.0               0.0   
4               0.0                     0.0               0.0   

   Australian Restaurant  Austrian Restaurant  Brazilian Restaurant  \
0                    0.0                  0.0                   0.0   
1                    0.0                  0.0                   0.0   
2                    0.0                  0.0                   0.0   
3                    0.0                  0.0                   0.0   
4                    0.0                  0.0                   0.0   

   Cajun / Creole Restaurant  Cambodian Restaurant  Cantonese Restaurant  \
0                        0.0                   0.0                   0.0   
1                        0.0                   0.0                   0.0   
2                        0.0                   0.0                   0.0   
3                        0.0                   0.0                   0.0   
4                        0.0                   0.0                   0.0   

   Caribbean Restaurant  Caucasian Restaurant  Chinese Restaurant  \
0                   0.0                   0.0            0.058824   
1                   0.0                   0.0            0.000000   
2                   0.0                   0.0            0.000000   
3                   0.0                   0.0            0.000000   
4                   0.0                   0.0            0.000000   

   Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
0                   0.0                      0.0               0.0   
1                   0.0                      0.0               0.0   
2                   0.0                      0.0               0.0   
3                   0.0                      0.0               0.0   
4                   0.0                      0.0               0.0   

   Czech Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
0               0.0                 0.0                  0.0   
1               0.0                 0.0                  0.0   
2               0.0                 0.0                  0.0   
3               0.0                 0.0                  0.0   
4               0.0                 0.0                  0.0   

   Eastern European Restaurant  Egyptian Restaurant  Empanada Restaurant  \
0                          0.0                  0.0                  0.0   
1                          0.0                  0.0                  0.0   
2                          0.0                  0.0                  0.0   
3                          0.0                  0.0                  0.0   
4                          0.0                  0.0                  0.0   

   English Restaurant  Ethiopian Restaurant  Falafel Restaurant  \
0                 0.0                   0.0                 0.0   
1                 0.0                   0.0                 0.0   
2                 0.0                   0.0                 0.0   
3                 0.0                   0.0                 0.0   
4                 0.0                   0.0                 0.0   

   Fast Food Restaurant  Filipino Restaurant  French Restaurant  \
0              0.029412                  0.0                0.0   
1              0.000000          

In [381]:
ny_restaurant['Asian Food'] = ny_restaurant['Asian Restaurant'] + ny_restaurant['Cantonese Restaurant'] + ny_restaurant['Chinese Restaurant'] + ny_restaurant['Dim Sum Restaurant'] + ny_restaurant['Dumpling Restaurant'] + ny_restaurant['Hotpot Restaurant'] + ny_restaurant['Shanghai Restaurant'] + ny_restaurant['Taiwanese Restaurant'] + ny_restaurant['Tibetan Restaurant'] + ny_restaurant['Japanese Curry Restaurant'] + ny_restaurant['Japanese Restaurant']+ ny_restaurant['Korean Restaurant'] + ny_restaurant['Sushi Restaurant'] + ny_restaurant['Udon Restaurant']+ ny_restaurant['Ramen Restaurant'] + ny_restaurant['Cambodian Restaurant']+ny_restaurant['Filipino Restaurant'] + ny_restaurant['Indonesian Restaurant'] + ny_restaurant['Malay Restaurant']+ny_restaurant['Pakistani Restaurant']+ny_restaurant['Sri Lankan Restaurant'] +ny_restaurant['Vietnamese Restaurant']+ny_restaurant['Thai Restaurant']+ny_restaurant['Szechuan Restaurant']+ny_restaurant['Sushi Restaurant']

In [382]:
ny_restaurant['Indian Food'] = ny_restaurant['Indian Restaurant']+ny_restaurant['South Indian Restaurant']+ny_restaurant['North Indian Restaurant']

In [383]:
ny_restaurant['European Food'] = ny_restaurant['Austrian Restaurant'] + ny_restaurant['Czech Restaurant']+ ny_restaurant['English Restaurant'] + ny_restaurant['French Restaurant'] + ny_restaurant['German Restaurant'] + ny_restaurant['Greek Restaurant'] + ny_restaurant['Modern European Restaurant'] + ny_restaurant['Scandinavian Restaurant'] + ny_restaurant['Russian Restaurant'] + ny_restaurant['Swiss Restaurant']+ny_restaurant['Italian Restaurant'] 

In [384]:
ny_restaurant['Latin American Food']= ny_restaurant['Argentinian Restaurant'] + ny_restaurant['Brazilian Restaurant']+ ny_restaurant['Cajun / Creole Restaurant']+ny_restaurant['Cuban Restaurant']+ny_restaurant['Latin American Restaurant']+ny_restaurant['Peruvian Restaurant']+ny_restaurant['South American Restaurant']

In [385]:
ny_restaurant['Middle Eastern Food'] = ny_restaurant['Egyptian Restaurant']+ny_restaurant['Kebab Restaurant']+ny_restaurant['Middle Eastern Restaurant']+ny_restaurant['Persian Restaurant']+ny_restaurant['Turkish Restaurant']

In [386]:
ny_restaurant['African Food'] = ny_restaurant['African Restaurant']+ny_restaurant['Egyptian Restaurant']+ny_restaurant['Ethiopian Restaurant']+ny_restaurant['Moroccan Restaurant']

In [387]:
ny_restaurant['Mediterranean Food'] = ny_restaurant['Mediterranean Restaurant']+ny_restaurant['Afghan Restaurant']+ny_restaurant['Israeli Restaurant']+ny_restaurant['Jewish Restaurant']+ny_restaurant['Kebab Restaurant']+ny_restaurant['Pakistani Restaurant']

In [388]:
ny_restaurant.head(5)

Neighborhood  Afghan Restaurant  African Restaurant  American Restaurant  \
0       Allerton                0.0                 0.0             0.000000   
1       Annadale                0.0                 0.0             0.076923   
2  Arden Heights                0.0                 0.0             0.000000   
3      Arlington                0.0                 0.0             0.125000   
4       Arrochar                0.0                 0.0             0.000000   

   Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  \
0               0.0                     0.0               0.0   
1               0.0                     0.0               0.0   
2               0.0                     0.0               0.0   
3               0.0                     0.0               0.0   
4               0.0                     0.0               0.0   

   Australian Restaurant  Austrian Restaurant  Brazilian Restaurant  \
0                    0.0                  0.0                   0.0   
1                    0.0                  0.0                   0.0   
2                    0.0                  0.0                   0.0   
3                    0.0                  0.0                   0.0   
4                    0.0                  0.0                   0.0   

   Cajun / Creole Restaurant  Cambodian Restaurant  Cantonese Restaurant  \
0                        0.0                   0.0                   0.0   
1                        0.0                   0.0                   0.0   
2                        0.0                   0.0                   0.0   
3                        0.0                   0.0                   0.0   
4                        0.0                   0.0                   0.0   

   Caribbean Restaurant  Caucasian Restaurant  Chinese Restaurant  \
0                   0.0                   0.0            0.058824   
1                   0.0                   0.0            0.000000   
2                   0.0                   0.0            0.000000   
3                   0.0                   0.0            0.000000   
4                   0.0                   0.0            0.000000   

   Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
0                   0.0                      0.0               0.0   
1                   0.0                      0.0               0.0   
2                   0.0                      0.0               0.0   
3                   0.0                      0.0               0.0   
4                   0.0                      0.0               0.0   

   Czech Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
0               0.0                 0.0                  0.0   
1               0.0                 0.0                  0.0   
2               0.0                 0.0                  0.0   
3               0.0                 0.0                  0.0   
4               0.0                 0.0                  0.0   

   Eastern European Restaurant  Egyptian Restaurant  Empanada Restaurant  \
0                          0.0                  0.0                  0.0   
1                          0.0                  0.0                  0.0   
2                          0.0                  0.0                  0.0   
3                          0.0                  0.0                  0.0   
4                          0.0                  0.0                  0.0   

   English Restaurant  Ethiopian Restaurant  Falafel Restaurant  \
0                 0.0                   0.0                 0.0   
1                 0.0                   0.0                 0.0   
2                 0.0                   0.0                 0.0   
3                 0.0                   0.0                 0.0   
4                 0.0                   0.0                 0.0   

   Fast Food Restaurant  Filipino Restaurant  French Restaurant  \
0              0.029412                  0.0                0.0   
1              0.000000          

In [389]:
ny_restaurant = ny_restaurant[['Neighborhood','Asian Food','Indian Food','European Food','Latin American Food','Middle Eastern Food','African Food','Mediterranean Food']]

In [390]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head(5)

Yoga Studio  Accessories Store  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0                 0                   0            0              0   
1                 0                   0            0              0   
2                 0                   0            0              0   
3                 0                   0            0              0   
4                 0                   0            0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0       0              0          0         0                     0   
1       0              0          0         0                     0   
2       0              0          0         0                     0   
3       0              0          0         0                     0   
4       0              0          0         0                     0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Building  \
0               0        0            0                0         0   
1               0        0            0                0         0   
2               0        0            0                0         0   
3               0        0            0                0         0   
4               0        0            0                0         0   

   Burger Joint  Burri

In [391]:
to_ground = toronto_onehot.groupby('Neighborhood').mean().reset_index()
to_ground.head(5)

Neighborhood  Yoga Studio  \
0                                        Agincourt          0.0   
1                           Alderwood, Long Branch          0.0   
2  Bathurst Manor, Wilson Heights, Downsview North          0.0   
3                                  Bayview Village          0.0   
4                Bedford Park, Lawrence Manor East          0.0   

   Accessories Store  Airport  Airport Food Court  Airport Gate  \
0                0.0      0.0                 0.0           0.0   
1                0.0      0.0                 0.0           0.0   
2                0.0      0.0                 0.0           0.0   
3                0.0      0.0                 0.0           0.0   
4                0.0      0.0                 0.0           0.0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0             0.0              0.0               0.0                 0.00   
1             0.0              0.0               0.0                 0.00   
2             0.0              0.0               0.0                 0.00   
3             0.0              0.0               0.0                 0.00   
4             0.0              0.0               0.0                 0.04   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0           0.0       0.0          0.0         0.0                  0.0   
1           0.0       0.0          0.0         0.0                  0.0   
2           0.0       0.0          0.0         0.0                  0.0   
3           0.0       0.0          0.0         0.0                  0.0   
4           0.0       0.0          0.0         0.0                  0.0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0               0.0                 0.0          0.0            0.0   
1               0.0                 0.0          0.0            0.0   
2               0.0                 0.0          0.0            0.0   
3               0.0                 0.0          0.0            0.0   
4               0.0                 0.0          0.0            0.0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery      Bank  Bar  Baseball Field  \
0        0.0         0.0         0.0     0.0  0.000000  0.0             0.0   
1        0.0         0.0         0.0     0.0  0.000000  0.0             0.0   
2        0.0         0.0         0.0     0.0  0.095238  0.0             0.0   
3        0.0         0.0         0.0     0.0  0.250000  0.0             0.0   
4        0.0         0.0         0.0     0.0  0.000000  0.0             0.0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0               0.0               0.0                 0.0    0.0   
1               0.0               0.0                 0.0    0.0   
2               0.0               0.0                 0.0    0.0   
3               0.0               0.0                 0.0    0.0   
4               0.0               0.0                 0.0    0.0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0              0.0       0.0         0.0                 0.0        0.0   
1              0.0       0.0         0.0                 0.0        0.0   
2              0.0       0.0         0.0                 0.0        0.0   
3              0.0       0.0         0.0                 0.0        0.0   
4              0.0       0.0         0.0                 0.0        0.0   

   Bistro  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0     0.0            0.0        0.0       0.0                   0.0   
1     0.0            0.0        0.0       0.0                   0.0   
2     0.0            0.0        0.0       0.0                   0.0   
3     0.0            0.0        0.0       0.0                   0.0   
4     0.0            0.0        0.0       0.0                   0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Building  \
0            0.25      0.0     0.000000              0.0   

In [392]:
filt = [x for x in to_ground.columns[to_ground.columns.str.contains('Restaurant')]]
to_rest = to_ground[filt]

In [393]:
to_restaurant = pd.concat([to_ground['Neighborhood'],to_rest],axis = 1,sort = False)

In [394]:
to_restaurant

Neighborhood  American Restaurant  \
0                                           Agincourt             0.000000   
1                              Alderwood, Long Branch             0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North             0.000000   
3                                     Bayview Village             0.000000   
4                   Bedford Park, Lawrence Manor East             0.040000   
5                                         Berczy Park             0.000000   
6                         Birch Cliff, Cliffside West             0.000000   
7        Brockton, Parkdale Village, Exhibition Place             0.000000   
8   Business reply mail Processing Centre, South C...             0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...             0.000000   
10                                Caledonia-Fairbanks             0.000000   
11              Canada Post Gateway Processing Centre             0.076923   
12                                          Cedarbrae             0.000000   
13                                 Central Bay Street             0.000000   
14                                           Christie             0.000000   
15                               Church and Wellesley             0.014085   
16            Clarks Corners, Tam O'Shanter, Sullivan             0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West             0.500000   
18                     Commerce Court, Victoria Hotel             0.040000   
19                                         Davisville             0.000000   
20                                   Davisville North             0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn             0.000000   
22                                          Don Mills             0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...             0.000000   
24                                          Downsview             0.000000   
25                       Dufferin, Dovercourt Village             0.000000   
26      East Toronto, Broadview North (Old East York)             0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...             0.000000   
28                       Fairview, Henry Farm, Oriole             0.015385   
29             First Canadian Place, Underground city             0.030000   
30    Forest Hill North & West, Forest Hill Road Park             0.000000   
31                           Garden District, Ryerson             0.000000   
32                                          Glencairn             0.000000   
33                    Golden Mile, Clairlea, Oakridge             0.000000   
34                  Guildwood, Morningside, West Hill             0.000000   
35  Harbourfront East, Union Station, Toronto Islands             0.000000   
36                      High Park, The Junction South             0.000000   
37                                  Hillcrest Village             0.000000   
38                                      Humber Summit             0.000000   
39                                   Humberlea, Emery             0.000000   
40                                 Humewood-Cedarvale             0.000000   
41                     India Bazaar, The Beaches West             0.000000   
42        Kennedy Park, Ionview, East Birchmount Park             0.000000   
43          Kensington Market, Chinatown, Grange Park             0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...             0.000000   
45                   Lawrence Manor, Lawrence Heights             0.000000   
46                                      Lawrence Park             0.000000   
47                                            Leaside             0.000000   
48                           Little Portugal, Trinity             0.000000   
49                                     Malvern, Rouge             0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...          

In [395]:
to_restaurant['Asian Food'] = to_restaurant['Asian Restaurant'] + to_restaurant['Chinese Restaurant'] + to_restaurant['Dim Sum Restaurant'] + to_restaurant['Dumpling Restaurant'] + to_restaurant['Taiwanese Restaurant'] + to_restaurant['Japanese Restaurant']+ to_restaurant['Korean Restaurant'] + to_restaurant['Sushi Restaurant'] + to_restaurant['Ramen Restaurant'] +to_restaurant['Filipino Restaurant'] + to_restaurant['Indonesian Restaurant'] +to_restaurant['Vietnamese Restaurant']+to_restaurant['Thai Restaurant']+to_restaurant['Sushi Restaurant']

In [396]:
to_restaurant['Indian Food'] = to_restaurant['Indian Restaurant']

In [397]:
to_restaurant['European Food'] = to_restaurant['French Restaurant'] + to_restaurant['German Restaurant'] + to_restaurant['Greek Restaurant'] + to_restaurant['Modern European Restaurant'] + to_restaurant['Portuguese Restaurant']+to_restaurant['Italian Restaurant'] 

In [398]:
to_restaurant['Latin American Food']= to_restaurant['Brazilian Restaurant']+ to_restaurant['Cajun / Creole Restaurant']+to_restaurant['Cuban Restaurant']+to_restaurant['Latin American Restaurant']

In [399]:
to_restaurant['Middle Eastern Food'] = to_restaurant['Middle Eastern Restaurant']+to_restaurant['Turkish Restaurant']

In [400]:
to_restaurant['African Food'] = to_restaurant['Ethiopian Restaurant']+to_restaurant['Moroccan Restaurant']

In [401]:
to_restaurant['Mediterranean Food'] = to_restaurant['Mediterranean Restaurant']

In [402]:
to_restaurant = to_restaurant[['Neighborhood','Asian Food','Indian Food','European Food','Latin American Food','Middle Eastern Food','African Food','Mediterranean Food']]

In [403]:
to_restaurant.describe()

Asian Food  Indian Food  European Food  Latin American Food  \
count   93.000000    93.000000      93.000000            93.000000   
mean     0.065378     0.007139       0.025871             0.005030   
std      0.105059     0.036587       0.069962             0.027454   
min      0.000000     0.000000       0.000000             0.000000   
25%      0.000000     0.000000       0.000000             0.000000   
50%      0.000000     0.000000       0.000000             0.000000   
75%      0.105263     0.000000       0.029412             0.000000   
max      0.500000     0.333333       0.500000             0.250000   

       Middle Eastern Food  African Food  Mediterranean Food  
count            93.000000     93.000000           93.000000  
mean              0.009758      0.000512            0.003499  
std               0.033903      0.002999            0.022307  
min               0.000000      0.000000            0.000000  
25%               0.000000      0.000000            0.000000  
50%               0.000000      0.000000            0.000000  
75%               0.000000      0.000000            0.000000  
max               0.250000      0.023529            0.200000

In [404]:
ny_restaurant.describe()

Asian Food  Indian Food  European Food  Latin American Food  \
count  302.000000   302.000000     302.000000           302.000000   
mean     0.067690     0.005133       0.034958             0.012813   
std      0.079889     0.021797       0.073963             0.031039   
min      0.000000     0.000000       0.000000             0.000000   
25%      0.000000     0.000000       0.000000             0.000000   
50%      0.049390     0.000000       0.000000             0.000000   
75%      0.105263     0.000000       0.052632             0.010446   
max      0.548387     0.250000       1.000000             0.287500   

       Middle Eastern Food  African Food  Mediterranean Food  
count           302.000000    302.000000          302.000000  
mean              0.003286      0.000952            0.003013  
std               0.012471      0.006588            0.009230  
min               0.000000      0.000000            0.000000  
25%               0.000000      0.000000            0.000000  
50%               0.000000      0.000000            0.000000  
75%               0.000000      0.000000            0.000000  
max               0.125000      0.088889            0.066667

In [468]:
to_restaurant

Neighborhood  Asian Food  \
0                                           Agincourt    0.000000   
1                              Alderwood, Long Branch    0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North    0.095238   
3                                     Bayview Village    0.500000   
4                   Bedford Park, Lawrence Manor East    0.120000   
5                                         Berczy Park    0.035088   
6                         Birch Cliff, Cliffside West    0.000000   
7        Brockton, Parkdale Village, Exhibition Place    0.000000   
8   Business reply mail Processing Centre, South C...    0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...    0.000000   
10                                Caledonia-Fairbanks    0.000000   
11              Canada Post Gateway Processing Centre    0.000000   
12                                          Cedarbrae    0.125000   
13                                 Central Bay Street    0.128571   
14                                           Christie    0.000000   
15                               Church and Wellesley    0.183099   
16            Clarks Corners, Tam O'Shanter, Sullivan    0.166667   
17    Cliffside, Cliffcrest, Scarborough Village West    0.000000   
18                     Commerce Court, Victoria Hotel    0.060000   
19                                         Davisville    0.151515   
20                                   Davisville North    0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn    0.000000   
22                                          Don Mills    0.222222   
23  Dorset Park, Wexford Heights, Scarborough Town...    0.333333   
24                                          Downsview    0.000000   
25                       Dufferin, Dovercourt Village    0.000000   
26      East Toronto, Broadview North (Old East York)    0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...    0.000000   
28                       Fairview, Henry Farm, Oriole    0.061538   
29             First Canadian Place, Underground city    0.130000   
30    Forest Hill North & West, Forest Hill Road Park    0.400000   
31                           Garden District, Ryerson    0.080000   
32                                          Glencairn    0.500000   
33                    Golden Mile, Clairlea, Oakridge    0.000000   
34                  Guildwood, Morningside, West Hill    0.000000   
35  Harbourfront East, Union Station, Toronto Islands    0.040000   
36                      High Park, The Junction South    0.083333   
37                                  Hillcrest Village    0.000000   
38                                      Humber Summit    0.000000   
39                                   Humberlea, Emery    0.000000   
40                                 Humewood-Cedarvale    0.000000   
41                     India Bazaar, The Beaches West    0.105263   
42        Kennedy Park, Ionview, East Birchmount Park    0.166667   
43          Kensington Market, Chinatown, Grange Park    0.092308   
44  Kingsview Village, St. Phillips, Martin Grove ...    0.000000   
45                   Lawrence Manor, Lawrence Heights    0.071429   
46                                      Lawrence Park    0.000000   
47                                            Leaside    0.060606   
48                           Little Portugal, Trinity    0.136364   
49                                     Malvern, Rouge    0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...    0.000000   
51                        Moore Park, Summerhill East    0.000000   
52       New Toronto, Mimico South, Humber Bay Shores    0.000000   
53           North Park, Maple Leaf Park, Upwood Park    0.000000   
54                 North Toronto West,  Lawrence Park    0.050000   
55                Northwest, West Humber - Clairville    0.000000   
56                    Northwood Park, York University    0.000000   
57  Old Mill South, King's Mill Park, S

In [469]:
to_restaurant['diversity_score'] = to_restaurant['Asian Food']+to_restaurant['Indian Food']+to_restaurant['European Food']+to_restaurant['Latin American Food']+to_restaurant['Middle Eastern Food']+to_restaurant['African Food']+to_restaurant['Mediterranean Food']

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [472]:
to_restaurant.head()

Neighborhood  Asian Food  Indian Food  \
0                                        Agincourt    0.000000         0.00   
1                           Alderwood, Long Branch    0.000000         0.00   
2  Bathurst Manor, Wilson Heights, Downsview North    0.095238         0.00   
3                                  Bayview Village    0.500000         0.00   
4                Bedford Park, Lawrence Manor East    0.120000         0.04   

   European Food  Latin American Food  Middle Eastern Food  African Food  \
0           0.00                 0.25             0.000000           0.0   
1           0.00                 0.00             0.000000           0.0   
2           0.00                 0.00             0.047619           0.0   
3           0.00                 0.00             0.000000           0.0   
4           0.12                 0.00             0.000000           0.0   

   Mediterranean Food  diversity_score  
0                 0.0         0.250000  
1                 0.0         0.000000  
2                 0.0         0.142857  
3                 0.0         0.500000  
4                 0.0         0.280000

In [473]:
to_restaurant_score = to_restaurant[['Neighborhood','diversity_score']]
to_restaurant_score

Neighborhood  diversity_score
0                                           Agincourt         0.250000
1                              Alderwood, Long Branch         0.000000
2     Bathurst Manor, Wilson Heights, Downsview North         0.142857
3                                     Bayview Village         0.500000
4                   Bedford Park, Lawrence Manor East         0.280000
5                                         Berczy Park         0.087719
6                         Birch Cliff, Cliffside West         0.000000
7        Brockton, Parkdale Village, Exhibition Place         0.041667
8   Business reply mail Processing Centre, South C...         0.000000
9   CN Tower, King and Spadina, Railway Lands, Har...         0.000000
10                                Caledonia-Fairbanks         0.000000
11              Canada Post Gateway Processing Centre         0.153846
12                                          Cedarbrae         0.125000
13                                 Central Bay Street         0.257143
14                                           Christie         0.058824
15                               Church and Wellesley         0.239437
16            Clarks Corners, Tam O'Shanter, Sullivan         0.250000
17    Cliffside, Cliffcrest, Scarborough Village West         0.000000
18                     Commerce Court, Victoria Hotel         0.100000
19                                         Davisville         0.272727
20                                   Davisville North         0.000000
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn         0.250000
22                                          Don Mills         0.259259
23  Dorset Park, Wexford Heights, Scarborough Town...         0.666667
24                                          Downsview         0.000000
25                       Dufferin, Dovercourt Village         0.071429
26      East Toronto, Broadview North (Old East York)         0.000000
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...         0.000000
28                       Fairview, Henry Farm, Oriole         0.061538
29             First Canadian Place, Underground city         0.170000
30    Forest Hill North & West, Forest Hill Road Park         0.400000
31                           Garden District, Ryerson         0.150000
32                                          Glencairn         0.500000
33                    Golden Mile, Clairlea, Oakridge         0.000000
34                  Guildwood, Morningside, West Hill         0.000000
35  Harbourfront East, Union Station, Toronto Islands         0.070000
36                      High Park, The Junction South         0.166667
37                                  Hillcrest Village         0.200000
38                                      Humber Summit         0.500000
39                                   Humberlea, Emery         0.000000
40                                 Humewood-Cedarvale         0.000000
41                     India Bazaar, The Beaches West         0.157895
42        Kennedy Park, Ionview, East Birchmount Park         0.166667
43          Kensington Market, Chinatown, Grange Park         0.092308
44  Kingsview Village, St. Phillips, Martin Grove ...         0.000000
45                   Lawrence Manor, Lawrence Heights         0.071429
46                                      Lawrence Park         0.000000
47                                            Leaside         0.060606
48                           Little Portugal, Trinity         0.227273
49                                     Malvern, Rouge         0.000000
50  Milliken, Agincourt North, Steeles East, L'Amo...         0.000000
51                        Moore Park, Summerhill East         0.000000
52       New Toronto, Mimico South, Humber Bay Shores         0.000000
53           North Park, Maple Leaf Park, Upwood Park         0.000000
54                 North Toronto West,  Lawrence Park         0.050000
55                Northwest, West Humber - Clairville         0.0

In [409]:
ny_restaurant['diversity_score'] = ny_restaurant['Asian Food']+ny_restaurant['Indian Food']+ny_restaurant['European Food']+ny_restaurant['Latin American Food']+ny_restaurant['Middle Eastern Food']+ny_restaurant['African Food']+ny_restaurant['Mediterranean Food']

In [483]:
ny_restaurant_score = ny_restaurant[['Neighborhood','diversity_score']]
ny_restaurant_score.head(5)

Neighborhood  diversity_score
0       Allerton         0.058824
1       Annadale         0.153846
2  Arden Heights         0.000000
3      Arlington         0.000000
4       Arrochar         0.190476

In [411]:
df_ny.shape

(306, 4)

In [412]:
ny_restaurant_score=pd.merge(ny_restaurant_score,df_ny,on='Neighborhood')

In [415]:
ny_restaurant_score = ny_restaurant_score[['Neighborhood','diversity_score','Latitude','Longitude']]

Neighborhood  diversity_score  \
0                                        Agincourt         0.250000   
1                           Alderwood, Long Branch         0.000000   
2  Bathurst Manor, Wilson Heights, Downsview North         0.142857   
3                                  Bayview Village         0.500000   
4                Bedford Park, Lawrence Manor East         0.280000   

    Latitude  Longitude  
0  43.794200 -79.262029  
1  43.602414 -79.543484  
2  43.754328 -79.442259  
3  43.786947 -79.385975  
4  43.733283 -79.419750

In [474]:
to_restaurant_score=pd.merge(to_restaurant_score,df_to,on='Neighborhood')
to_restaurant_score

Neighborhood  diversity_score  \
0                                           Agincourt         0.250000   
1                              Alderwood, Long Branch         0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North         0.142857   
3                                     Bayview Village         0.500000   
4                   Bedford Park, Lawrence Manor East         0.280000   
5                                         Berczy Park         0.087719   
6                         Birch Cliff, Cliffside West         0.000000   
7        Brockton, Parkdale Village, Exhibition Place         0.041667   
8   Business reply mail Processing Centre, South C...         0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...         0.000000   
10                                Caledonia-Fairbanks         0.000000   
11              Canada Post Gateway Processing Centre         0.153846   
12                                          Cedarbrae         0.125000   
13                                 Central Bay Street         0.257143   
14                                           Christie         0.058824   
15                               Church and Wellesley         0.239437   
16            Clarks Corners, Tam O'Shanter, Sullivan         0.250000   
17    Cliffside, Cliffcrest, Scarborough Village West         0.000000   
18                     Commerce Court, Victoria Hotel         0.100000   
19                                         Davisville         0.272727   
20                                   Davisville North         0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn         0.250000   
22                                          Don Mills         0.259259   
23                                          Don Mills         0.259259   
24  Dorset Park, Wexford Heights, Scarborough Town...         0.666667   
25                                          Downsview         0.000000   
26                                          Downsview         0.000000   
27                                          Downsview         0.000000   
28                                          Downsview         0.000000   
29                       Dufferin, Dovercourt Village         0.071429   
30      East Toronto, Broadview North (Old East York)         0.000000   
31  Eringate, Bloordale Gardens, Old Burnhamthorpe...         0.000000   
32                       Fairview, Henry Farm, Oriole         0.061538   
33             First Canadian Place, Underground city         0.170000   
34    Forest Hill North & West, Forest Hill Road Park         0.400000   
35                           Garden District, Ryerson         0.150000   
36                                          Glencairn         0.500000   
37                    Golden Mile, Clairlea, Oakridge         0.000000   
38                  Guildwood, Morningside, West Hill         0.000000   
39  Harbourfront East, Union Station, Toronto Islands         0.070000   
40                      High Park, The Junction South         0.166667   
41                                  Hillcrest Village         0.200000   
42                                      Humber Summit         0.500000   
43                                   Humberlea, Emery         0.000000   
44                                 Humewood-Cedarvale         0.000000   
45                     India Bazaar, The Beaches West         0.157895   
46        Kennedy Park, Ionview, East Birchmount Park         0.166667   
47          Kensington Market, Chinatown, Grange Park         0.092308   
48  Kingsview Village, St. Phillips, Martin Grove ...         0.000000   
49                   Lawrence Manor, Lawrence Heights         0.071429   
50                                      Lawrence Park         0.000000   
51                                            Leaside         0.060606   
52                           Little Portugal, Trinity         0.227273   
53                                     Malver

In [475]:
to_restaurant_score = to_restaurant_score[['Postal Code','diversity_score','Latitude','Longitude']]

In [476]:
to_restaurant_score.head()

Postal Code  diversity_score   Latitude  Longitude
0         M1S         0.250000  43.794200 -79.262029
1         M8W         0.000000  43.602414 -79.543484
2         M3H         0.142857  43.754328 -79.442259
3         M2K         0.500000  43.786947 -79.385975
4         M5M         0.280000  43.733283 -79.419750

In [421]:
ny_restaurant_score

Neighborhood  diversity_score   Latitude  Longitude
0                     Allerton         0.058824  40.865788 -73.859319
1                     Annadale         0.153846  40.538114 -74.178549
2                Arden Heights         0.000000  40.549286 -74.185887
3                    Arlington         0.000000  40.635325 -74.165104
4                     Arrochar         0.190476  40.596313 -74.067124
5                      Arverne         0.050000  40.589144 -73.791992
6                      Astoria         0.300000  40.768509 -73.915654
7              Astoria Heights         0.166667  40.770317 -73.894680
8                   Auburndale         0.263158  40.761730 -73.791762
9                   Bath Beach         0.360000  40.599519 -73.998752
10           Battery Park City         0.058824  40.711932 -74.016869
11                   Bay Ridge         0.238095  40.625801 -74.030621
12                 Bay Terrace         0.061224  40.782843 -73.776802
13                 Bay Terrace         0.061224  40.553988 -74.139166
14                  Baychester         0.000000  40.866858 -73.835798
15                     Bayside         0.315789  40.766041 -73.774274
16                   Bayswater         0.000000  40.611322 -73.765968
17                Bedford Park         0.131579  40.870185 -73.885512
18          Bedford Stuyvesant         0.034483  40.687232 -73.941785
19                  Beechhurst         0.200000  40.792781 -73.804365
20                    Bellaire         0.307692  40.733014 -73.738892
21                Belle Harbor         0.117647  40.576156 -73.854018
22                   Bellerose         0.125000  40.728573 -73.720128
23                     Belmont         0.190000  40.857277 -73.888452
24                 Bensonhurst         0.357143  40.611009 -73.995180
25                Bergen Beach         0.000000  40.615150 -73.898556
26                  Blissville         0.062500  40.737251 -73.932442
27                  Bloomfield         0.000000  40.605779 -74.187256
28                 Boerum Hill         0.147727  40.685683 -73.983748
29                Borough Park         0.000000  40.633131 -73.990498
30                Breezy Point         0.000000  40.557401 -73.925512
31                   Briarwood         0.125000  40.710935 -73.811748
32              Brighton Beach         0.204545  40.576825 -73.965094
33               Broad Channel         0.000000  40.603027 -73.820055
34           Broadway Junction         0.000000  40.677861 -73.903317
35                   Bronxdale         0.230769  40.852723 -73.861726
36            Brooklyn Heights         0.170000  40.695864 -73.993782
37                  Brookville         0.000000  40.660003 -73.751753
38                 Brownsville         0.133333  40.663950 -73.910235
39                  Bulls Head         0.155556  40.609592 -74.159409
40                    Bushwick         0.083333  40.698116 -73.925258
41                Butler Manor         0.000000  40.506082 -74.229504
42             Cambria Heights         0.076923  40.692775 -73.735269
43                    Canarsie         0.400000  40.635564 -73.902093
44               Carnegie Hill         0.147368  40.782683 -73.953256
45             Carroll Gardens         0.220000  40.680540 -73.994654
46                 Castle Hill         0.111111  40.819014 -73.848027
47           Castleton Corners         0.058824  40.613336 -74.119181
48              Central Harlem         0.177778  40.815976 -73.943211
49                  Charleston         0.064516  40.530531 -74.232158
50                     Chelsea         0.095238  40.594726 -74.189560
51                     Chelsea         0.095238  40.744035 -74.003116
52                   Chinatown         0.290000  40.715618 -73.994279
53                 City Island         0.071429  40.847247 -73.786488
54                   City Line         0.085714  40.678570 -73.867976
55                Civic Center         0.160000  40.715229 -74.005415
56           Claremont Villa

In [454]:
world_geo = r'd085e2f8d0b54d4590b1e7d1f35594c1pediacitiesnycneighborhoods.geojson.json' # geojson file

map_newyork = folium.Map(location=[latitude_ny, longitude_ny], zoom_start=10.5)

In [456]:

map_newyork.choropleth(
    geo_data=world_geo,
    data=ny_restaurant_score,
    columns=['Neighborhood', 'diversity_score'],
    key_on='feature.properties.neighborhood',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Diversity Score of New York City'
)


# display map
map_newyork

In [485]:
world_geo = r'Toronto2.geo.json' # geojson file

map_toronto = folium.Map(location=[latitude_to, longitude_to], zoom_start=10.5)

In [486]:

map_toronto.choropleth(
    geo_data=world_geo,
    data=to_restaurant_score,
    columns=['Postal Code', 'diversity_score'],
    key_on='feature.properties.CFSAUID',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Diversity Score of Toronto'
)


# display map
map_toronto